In [15]:
import numpy as np
import pandas as pd
from scipy.optimize import curve_fit
import glob
import os

def heaps_exchange(x, alfa, theta):
    return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa

def analyze_heaps_files():
    # Trova tutti i file che iniziano con "heaps" e finiscono con ".txt"
    heaps_files = glob.glob("HEAPS/heaps*.txt")
    
    if not heaps_files:
        print("Nessun file heaps*.txt trovato nella directory corrente")
        return
    
    # Definisci nu e rho
    nu = np.arange(1, 50)
    rho = np.arange(2, 51)
    
    results = []
    
    for filename in heaps_files:
        try:
            # Leggi il file
            data = pd.read_csv(filename, sep='\s+', header=None, names=['x', 'y'])
            
            # Estrai nome senza prefisso "heaps_" e suffisso ".txt"
            base_name = os.path.basename(filename)
            if base_name.startswith('heaps_'):
                name_without_prefix = base_name[6:]  # Rimuovi "heaps_"
            else:
                name_without_prefix = base_name
            
            if name_without_prefix.endswith('.txt'):
                name_without_prefix = name_without_prefix[:-4]  # Rimuovi ".txt"
            
            # Esegui il fitting
            x_data = data['x'].values
            y_data = data['y'].values
            
            # Parametri iniziali per il fitting
            p0 = [0.5, 100]  # valori iniziali per alfa e theta
            
            try:
                # Curve fitting
                popt, pcov = curve_fit(heaps_exchange, x_data, y_data, p0=p0, maxfev=5000)
                alfa_fit, theta_fit = popt
                
                # Trova nu e rho tali che nu/rho sia il più vicino possibile a alfa
                best_diff = float('inf')
                best_nu = None
                best_rho = None
                
                for n in nu:
                    for r in rho:
                        ratio = n / r
                        diff = abs(ratio - alfa_fit)
                        if diff < best_diff:
                            best_diff = diff
                            best_nu = n
                            best_rho = r
                
                # Calcola N0
                N0 = int(best_rho * theta_fit)
                
                # Lunghezza della sequenza
                sequence_length = len(data)
                
                # Controlli per escludere sequenze non valide
                if N0 <= 0:
                    print(f"Saltato {filename}: N0={N0} (valore nullo)")
                    continue
                
                if N0 > 1000000:
                    print(f"Saltato {filename}: N0={N0} (troppo grande)")
                    continue
                
                if sequence_length < 500:
                    print(f"Saltato {filename}: lunghezza={sequence_length} (troppo corta)")
                    continue
                
                # Aggiungi ai risultati
                results.append({
                    'filename': name_without_prefix,
                    'nu': best_nu,
                    'rho': best_rho,
                    'N0': N0,
                    'length': sequence_length,
                    'alfa': alfa_fit,
                    'theta': theta_fit
                })
                
                print(f"Processato {filename}: alfa={alfa_fit:.4f}, theta={theta_fit:.4f}, N0={N0}")
                
            except Exception as e:
                print(f"Errore nel fitting di {filename}: {e}")
                continue
                
        except Exception as e:
            print(f"Errore nel leggere {filename}: {e}")
            continue
    
    # Scrivi i risultati nel file di output
    if results:
        with open('heaps_analysis_results_shorter_than_1000.txt', 'w') as f:
            f.write("filename\tnu\trho\tN0\tlength\n")
            for result in results:
                f.write(f"{result['filename']}\t{result['nu']}\t{result['rho']}\t{result['N0']}\t{result['length']}\n")
        
        print(f"\nRisultati salvati in 'heaps_analysis_results.txt'")
        print(f"Processati {len(results)} file con successo")
        
        # Mostra un'anteprima dei risultati
        print("\nAnteprima risultati:")
        print("filename\tnu\trho\tN0\tlength")
        for result in results[:5]:  # Mostra solo i primi 5
            print(f"{result['filename']}\t{result['nu']}\t{result['rho']}\t{result['N0']}\t{result['length']}")
        if len(results) > 5:
            print("...")
    else:
        print("Nessun file processato con successo")


<>:27: SyntaxWarning: invalid escape sequence '\s'
<>:27: SyntaxWarning: invalid escape sequence '\s'
/tmp/ipykernel_1723212/1151214657.py:27: SyntaxWarning: invalid escape sequence '\s'
  data = pd.read_csv(filename, sep='\s+', header=None, names=['x', 'y'])


In [16]:
analyze_heaps_files()

Saltato HEAPS/heaps_text_11825.txt: lunghezza=370 (troppo corta)
Saltato HEAPS/heaps_text_8172.txt: lunghezza=285 (troppo corta)
Saltato HEAPS/heaps_text_26498.txt: lunghezza=271 (troppo corta)
Saltato HEAPS/heaps_text_26620.txt: lunghezza=352 (troppo corta)
Saltato HEAPS/heaps_text_488.txt: lunghezza=267 (troppo corta)
Processato HEAPS/heaps_text_14432.txt: alfa=0.7817, theta=91.7481, N0=2935
Saltato HEAPS/heaps_text_15489.txt: lunghezza=383 (troppo corta)
Saltato HEAPS/heaps_text_18863.txt: N0=0 (valore nullo)
Saltato HEAPS/heaps_text_17981.txt: lunghezza=293 (troppo corta)
Saltato HEAPS/heaps_text_21189.txt: lunghezza=210 (troppo corta)
Saltato HEAPS/heaps_text_6798.txt: lunghezza=320 (troppo corta)
Processato HEAPS/heaps_text_22035.txt: alfa=0.8379, theta=7.3756, N0=272
Processato HEAPS/heaps_text_21216.txt: alfa=0.7102, theta=16.6187, N0=631
Saltato HEAPS/heaps_text_3800.txt: N0=0 (valore nullo)
Saltato HEAPS/heaps_text_23456.txt: lunghezza=433 (troppo corta)
Processato HEAPS/heap

/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta

Errore nel fitting di HEAPS/heaps_text_31622.txt: Optimal parameters not found: Number of calls to function has reached maxfev = 5000.
Saltato HEAPS/heaps_text_7601.txt: lunghezza=357 (troppo corta)
Saltato HEAPS/heaps_text_5028.txt: lunghezza=423 (troppo corta)
Saltato HEAPS/heaps_text_1907.txt: lunghezza=420 (troppo corta)
Saltato HEAPS/heaps_text_36020.txt: lunghezza=184 (troppo corta)
Saltato HEAPS/heaps_text_205.txt: lunghezza=369 (troppo corta)
Saltato HEAPS/heaps_text_19141.txt: lunghezza=244 (troppo corta)
Processato HEAPS/heaps_text_2112.txt: alfa=0.8333, theta=16.0738, N0=96
Processato HEAPS/heaps_text_14827.txt: alfa=0.7475, theta=63.6663, N0=254
Processato HEAPS/heaps_text_13333.txt: alfa=0.7233, theta=59.9352, N0=2816
Saltato HEAPS/heaps_text_13098.txt: lunghezza=246 (troppo corta)
Saltato HEAPS/heaps_text_19251.txt: lunghezza=270 (troppo corta)
Saltato HEAPS/heaps_text_4413.txt: lunghezza=355 (troppo corta)
Saltato HEAPS/heaps_text_32852.txt: lunghezza=412 (troppo corta)


/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta

Saltato HEAPS/heaps_text_3596.txt: N0=0 (valore nullo)
Saltato HEAPS/heaps_text_33270.txt: N0=0 (valore nullo)
Processato HEAPS/heaps_text_19706.txt: alfa=0.7459, theta=24.3642, N0=1145
Processato HEAPS/heaps_text_8768.txt: alfa=0.9230, theta=1.4246, N0=18
Processato HEAPS/heaps_text_22877.txt: alfa=0.7169, theta=10.6458, N0=489
Errore nel fitting di HEAPS/heaps_text_14558.txt: Optimal parameters not found: Number of calls to function has reached maxfev = 5000.
Saltato HEAPS/heaps_text_20380.txt: lunghezza=483 (troppo corta)
Saltato HEAPS/heaps_text_22449.txt: lunghezza=385 (troppo corta)
Processato HEAPS/heaps_text_3283.txt: alfa=0.7946, theta=15.8661, N0=618
Saltato HEAPS/heaps_text_34674.txt: lunghezza=472 (troppo corta)
Saltato HEAPS/heaps_text_6588.txt: lunghezza=488 (troppo corta)
Saltato HEAPS/heaps_text_16022.txt: N0=0 (valore nullo)
Saltato HEAPS/heaps_text_22706.txt: lunghezza=303 (troppo corta)
Saltato HEAPS/heaps_text_35271.txt: lunghezza=485 (troppo corta)
Saltato HEAPS/he

...

/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta

Processato HEAPS/heaps_text_35163.txt: alfa=0.8606, theta=9.8245, N0=422
Saltato HEAPS/heaps_text_26680.txt: lunghezza=234 (troppo corta)
Processato HEAPS/heaps_text_4144.txt: alfa=0.8418, theta=20.0313, N0=380
Saltato HEAPS/heaps_text_14233.txt: lunghezza=197 (troppo corta)
Saltato HEAPS/heaps_text_3645.txt: lunghezza=365 (troppo corta)
Saltato HEAPS/heaps_text_16287.txt: lunghezza=348 (troppo corta)
Processato HEAPS/heaps_text_18423.txt: alfa=0.7981, theta=14.0234, N0=70
Processato HEAPS/heaps_text_28445.txt: alfa=0.8009, theta=11.5621, N0=57
Saltato HEAPS/heaps_text_19478.txt: lunghezza=227 (troppo corta)
Saltato HEAPS/heaps_text_754.txt: lunghezza=208 (troppo corta)
Processato HEAPS/heaps_text_36542.txt: alfa=0.7770, theta=19.1220, N0=172
Saltato HEAPS/heaps_text_38503.txt: lunghezza=386 (troppo corta)
Processato HEAPS/heaps_text_13284.txt: alfa=0.8727, theta=11.6775, N0=548
Processato HEAPS/heaps_text_24322.txt: alfa=0.7609, theta=37.9836, N0=1747
Processato HEAPS/heaps_text_22100

/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta

Processato HEAPS/heaps_text_20650.txt: alfa=0.7800, theta=34.3294, N0=1716
Saltato HEAPS/heaps_text_30270.txt: lunghezza=214 (troppo corta)
Errore nel fitting di HEAPS/heaps_text_30752.txt: Optimal parameters not found: Number of calls to function has reached maxfev = 5000.
Errore nel fitting di HEAPS/heaps_text_182.txt: Optimal parameters not found: Number of calls to function has reached maxfev = 5000.
Saltato HEAPS/heaps_text_8008.txt: lunghezza=185 (troppo corta)
Saltato HEAPS/heaps_text_11048.txt: lunghezza=389 (troppo corta)
Saltato HEAPS/heaps_text_30712.txt: lunghezza=315 (troppo corta)
Processato HEAPS/heaps_text_38611.txt: alfa=0.7790, theta=11.0702, N0=553
Processato HEAPS/heaps_text_32155.txt: alfa=0.7594, theta=19.5102, N0=487
Processato HEAPS/heaps_text_2177.txt: alfa=0.7715, theta=29.9583, N0=1048
Saltato HEAPS/heaps_text_28266.txt: N0=949895037 (troppo grande)
Saltato HEAPS/heaps_text_6883.txt: N0=0 (valore nullo)
Processato HEAPS/heaps_text_20936.txt: alfa=0.9236, thet

/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta)**alfa) - theta/alfa
/tmp/ipykernel_1723212/1151214657.py:8: RuntimeWarning: invalid value encountered in power
  return (theta/alfa)*((1+x/theta